In [ ]:
%pip install sentence-transformers==2.0.0

https://www.kaggle.com/datasets/dataranch/upwork-1

1. Load dataset with pandas

In [135]:
import pandas as pd

df = pd.read_csv('freelancers.csv')
df = df[['shortName', 'title', 'description', 'location', 'hourlyRate', 'avgFeedbackScore', 'skills']]
df = df.dropna(subset='skills')
df = df.dropna(subset='title')
df['location'] = df['location'].apply(lambda x : eval(x)['state'])
df['skills'] = df['skills'].apply(lambda x : [x['skill']['name'] for x in eval(x)])
df['hourlyRate'] = df['hourlyRate'].apply(lambda x : eval(x)['amount'])

In [ ]:
def keyword_extractor(total_keywords, str1):
    word_list = list()
    for keyword in total_keywords:
        for word in str1.split(' '):
            if word == keyword:
                word_list.append(word)
    return word_list
total_keywords = df.explode('skills')['skills'].unique().tolist()

skill_keywords = keyword_extractor(total_keywords, 'I want to hire a wordpress')
df[df['skills'].apply(lambda x: all(val in x for val in skill_keywords))]

2. Encode 100 samples into vectors (1 column with product text, 1 column with vectors)

In [136]:
import pandas as pd
from tqdm import tqdm
from sentence_transformers import SentenceTransformer
tqdm.pandas()

model = SentenceTransformer('all-mpnet-base-v2') #all-MiniLM-L6-v2 #all-mpnet-base-v2

#encode df version: for small dataset only
df['text_vector_'] = df['title'].progress_apply(lambda x : model.encode(x).tolist())
df

100%|██████████| 5815/5815 [12:10<00:00,  7.96it/s]


shortName                                              title  \
0        Jason V.                         Expert WordPress Developer   
1      Miranda S.                               Social Media Manager   
2      Gagan S J.                                 Solution Architect   
3       Roxana L.  Procurement, Logistics and Supply Chain profes...   
4         John M.  3d generalist, post production artist and Vide...   
...           ...                                                ...   
5818     Megan D.  Web Research/Content Curation/Data Entry/Socia...   
5819    Austin V.                                    Product Manager   
5820      Eric M.        Web Developer/Designer And Graphic Designer   
5821  Kristina A.  Voice Over Talent, video editing, video produc...   
5822    Ashley C.                  Print and Digital Layout Designer   

                                            description location  hourlyRate  \
0     Hello! Welcome to my profile!\n\nMy name is Ja...       IL       60.00   
1     I am a Social Media Manager who specializes in...       NY       20.00   
2     More than 25 years in IT with 20 years in US h...       NJ       65.00   
3     I work FAST - I am COST EFFICIENT - I deliver ...       NC       70.00   
4     I am a 3D artist, animator, and designer with ...       OK       50.00   
...                                                 ...      ...         ...   
5818  Extremely driven, yet easy-going gal who refus...       CA       22.37   
5819  Experienced in building and growing digital pl...       AZ      100.00   
5820  4 YEARS experience in  Wordpress / Shopify / D...       OH       25.00   
5821  A musician from birth. I studied music educati...       VA       60.00   
5822  Hello, I'm Ashley, a professional designer and...       OR       25.00   

      avgFeedbackScore                                             skills  \
0             4.925208  [wordpress, seo, wp-ecommerce, woocommerce, bo...   
1             4.675676  [social-media-content-creation, video-editing,...   
2             0.000000  [oracle-java-ee, spring-framework, hibernate, ...   
3             4.916684  [procurement-function, pharmaceutical-industry...   
4             5.000000  [animation, motion-graphics, video-editing, vi...   
...                ...                                                ...   
5818          4.574029  [data-entry, internet-research, virtual-assist...   
5819          0.000000  [atlassian-jira, atlassian-confluence, project...   
5820          4.451507  [html, css, wordpress, shopify, joomla, drupal...   
5821          5.000000                                       [articulate]   
5822          4.951186  [print-layout-design, brochure-design, flyer-d...   

                                           text_vector_  
0     [0.078628771007061, 0.024731114506721497, -0.0...  
1     [0.07423530519008636, -0.022386642172932625, -...  
2     [0.04637446999549866, 0.03554175794124603, -0....  
3     [0.026502298191189766, -0.02052873745560646, -...  
4     [0.05356863886117935, 0.032190944999456406, -0...  
...                                                 ...  
5818  [0.07812528312206268, -0.018792806193232536, -...  
5819  [0.056266412138938904, -0.007661229465156794, ...  
5820  [0.048749279230833054, -0.013894445262849331, ...  
5821  [0.03207482025027275, -0.027680398896336555, -...  
5822  [0.04141489043831825, -0.04500063508749008, -0...  

[5815 rows x 8 columns]

In [133]:
import random

df = df.drop_duplicates(subset=['shortName', 'location', 'title', 'hourlyRate', 'avgFeedbackScore', 'description'])
df = df.reset_index(drop=True)
df['location'] = df['location'].apply(lambda x : random.choice(['New York', 'Chicago', 'Washington']))
df.to_parquet('df_encoded.parquet', index=None)